In [26]:
import pandas as pd
import requests
import json

In [27]:
model = '/models/Qwen3-30B-A3B-Instruct-2507-FP8'
url = 'https://10.44.123.3/qwen30-fp8/v1/chat/completions'

def call_llm(model, url, sys_prompt, user_prompt):
    payload = {
                "model": model,
                "messages": [
                    {"role": "system", "content": sys_prompt},
                    {"role": "user", "content": user_prompt},
                ],
                "temperature": 0.1,
                "stream": False,
                "chat_template_kwargs": {"enable_thinking": False},
            }
    url = url
    response = requests.post(url=url, json=payload, verify=False, timeout=120).json()
    resp = response['choices'][0]['message']['content']
    return resp

In [28]:
with open('1_VOP.md', encoding='utf8') as file:
    text = file.read()

In [29]:
# парсим файл с вопросно-ответными парами
lines = text.split('\n')

text_data = []

current_question = None
current_answer = []

for line in lines:
    if line.startswith('## '):
        if current_question is not None:
            text_data.append([current_question, ' '.join(current_answer)])
            current_answer = []
        current_question = line[3:].strip()
    else:
        current_answer.append(line.strip())

if current_question is not None:
    text_data.append([current_question, ' '.join(current_answer)])
text_data
# df = pd.DataFrame(text_data[:10], columns=['Вопрос', 'Ответ'])
# df

[['Добрый день! Приводим в соответствие сведения о ВРИ на з/у общего пользования в СНТ(к.н 50:26:0180417:101) Просим пояснить: будет ли начислена плата как за изменение ВРИ при обращении за государственной услугой об установлении соответствия ВРИ ( на текущий момент требуется внести изменения с ВРИ "для садоводства" на ВРИ с кодификацией 13.2-"ведение садоводства"). Процедура изменения ВРИ в данном случае предусматривает внесение платы. Будет ли при взиматься плата, если мы воспользуемся госуслугой "установление соответствия" ввиду того, что в действующих ПЗЗ отсутствует имеющийся вид разрешенного использования ("для садоводства")',
  'Добрый день! Информируем, что за изменение ВРИ на виды предусматривающие жилищное строительство  взимается плата, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57. Первоначально необходимо обратиться за услугой "Предоставление расчета размера платы за изменение ВРИ земельного участка". Сс

In [30]:
# делаем из ВОП словари с дубликатами ответов и уникальными ответами
from collections import defaultdict

def group_by_identical_answers(text_data: list):
    """
    На входе список списков, каждый маленький список - вопрос + ответ
    На выходе:
        duplicates: dict {answer: [question1, question2, ...]} для ответов, которые соответствуют >1 вопросу
        unique: список [[question, answer]] для уникальных ответов
    """
    def normalize_answer(answer):
        return ' '.join(answer.strip().split())
    
    answer_groups = defaultdict(list)
    
    for question, answer in text_data:
        norm_answer = normalize_answer(answer)
        answer_groups[norm_answer].append({
            'question': question,
            'original_answer': answer  
        })
    
    # Разделение на группы
    duplicate_qa_groups = []
    unique_qa_pairs = []
    
    for norm_answer, items in answer_groups.items():
        if len(items) > 1:
            duplicate_qa_groups.append({
                'answer': norm_answer,
                # 'original_answer': items[0]['original_answer'],  # Берём первый оригинальный ответ
                'questions': [item['question'] for item in items],
                # 'count': len(items),
                # 'raw_items': items  # Все оригинальные данные
            })
        else:
            unique_qa_pairs.append([items[0]['question'], items[0]['original_answer']])
    
    return duplicate_qa_groups, unique_qa_pairs

# Использование
duplicate_groups, unique_pairs = group_by_identical_answers(text_data)

# Статистика
print(f"Всего пар: {len(text_data)}")
print(f"Уникальных ответов: {len(unique_pairs)}")
print(f"Групп с одинаковыми ответами: {len(duplicate_groups)}")


Всего пар: 838
Уникальных ответов: 411
Групп с одинаковыми ответами: 60


## Работа с дубликатами

In [31]:
duplicate_groups

[{'answer': 'Добрый день! Информируем, что за изменение ВРИ на виды предусматривающие жилищное строительство взимается плата, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57. Первоначально необходимо обратиться за услугой "Предоставление расчета размера платы за изменение ВРИ земельного участка". Ссылка на услугу – "https://uslugi.mosreg.ru/services/21663" . Далее, после оплаты Вам необходимо обратиться в Управление Федеральной службы государственной регистрации, кадастра и картографии по Московской области (Росреестр), посредством обращения в любой центр государственных и муниципальных услуг "Мои документы" на территории Московской области за изменением вида разрешенного использования земельного участка.',
  'questions': ['Добрый день! Приводим в соответствие сведения о ВРИ на з/у общего пользования в СНТ(к.н 50:26:0180417:101) Просим пояснить: будет ли начислена плата как за изменение ВРИ при обращении за государстве

In [32]:
sys_prompt = '''
Ты получаешь на вход группу вопросов с одинаковым ответом.

Структура входных данных:
{
  "answer": "универсальный ответ на все вопросы",
  "questions": ["список вопросов"]
}

Твоя задача:
ШАГ 1: Определи общую тему всех вопросов (максимум 3 слова)
ШАГ 2: Сгруппируй вопросы по подтемам. Для каждой группы выдели:
- Название подтемы
- Количество вопросов
- Что объединяет эти вопросы
ШАГ 3: На основе исходных вопросов темы и универсального ответа составь эталонные вопросы для каждой подтемы (до 2 вопросов на подтему). Ответ должен хотя бы примерно соответствовать эталонным вопросам.


ФОРМАТ ОТВЕТА - ТОЛЬКО чистый JSON:
{
  "analysis": {
    "general_topic": "общая тема всех вопросов (1-2 слова)",
    "answer": "оригинальный универсальный ответ"
  },
  "themes": [
    {
      "theme_name": "Название тематики",
      "question_count": число,
      "description": "краткое описание тематики"
      "canonical_questions": ["созданные эталонные вопросы (1-2 штуки)"],
    }
  ],
}

ВАЖНЫЕ ПРАВИЛА:
1. Ответ ТОЛЬКО в этом JSON-формате, без пояснений
2. canonical_questions должны быть четкими, без конкретных имён/дат/адресов
3. Если вопросы очень похожи, можно оставить 1-2 эталонных
4. Общая тема (general_topic) должна быть краткой
'''

In [33]:
# анализируем дубликаты
duplicate_lst = []
for elem in duplicate_groups:
    user_prompt = f'Группа вопросов: {elem}'
    resp = call_llm(model, url, sys_prompt, user_prompt)
    duplicate_lst.append(resp)
# duplicate_lst

c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: Insecur

In [34]:
# придаем ответу вид JSONа
import re
from typing import Any, Optional

def clean_and_parse_json(json_like_string: str) -> Optional[Any]:
    """
    Очищает и парсит строку, похожую на JSON, даже с проблемами.
    Обрабатывает:
    - Строки внутри списков Python ['{...}']
    - Проблемы с экранированием кавычек
    - Лишние символы
    """
    if not json_like_string:
        return None
    
    # Если это список Python, извлекаем первый элемент
    if json_like_string.startswith('[') and json_like_string.endswith(']'):
        try:
            # Безопасно извлекаем содержимое
            match = re.search(r'\[(.*)\]', json_like_string, re.DOTALL)
            if match:
                json_like_string = match.group(1).strip()
        except:
            pass
    
    # Убираем возможные лишние кавычки в начале/конце
    json_like_string = json_like_string.strip()
    if json_like_string.startswith("'") and json_like_string.endswith("'"):
        json_like_string = json_like_string[1:-1]
    elif json_like_string.startswith('"') and json_like_string.endswith('"'):
        json_like_string = json_like_string[1:-1]
    
    # Исправляем двойное экранирование (\\")
    # Заменяем \\" на \"
    json_like_string = re.sub(r'\\\\"', r'\\"', json_like_string)
    
    # Убираем лишние обратные слэши перед кавычками
    json_like_string = re.sub(r'\\+(")', r'\\\1', json_like_string)
    
    # Пробуем распарсить
    try:
        return json.loads(json_like_string)
    except json.JSONDecodeError as e:
        # Пробуем исправить наиболее частые ошибки
        print(f"Первая попытка не удалась: {e}")
        
        # Исправляем незакрытые кавычки в длинных строках
        # Находим все строки в JSON и проверяем их
        try:
            # Убираем проблемные символы
            json_like_string = re.sub(r'([^\\])"([^\\])"', r'\1"\2"', json_like_string)
            
            # Пробуем снова
            return json.loads(json_like_string)
        except json.JSONDecodeError:
            # Последняя попытка: находим JSON объект в строке
            match = re.search(r'\{.*\}', json_like_string, re.DOTALL)
            if match:
                try:
                    return json.loads(match.group())
                except:
                    pass
    
    return None

cleaned_duplicate_list = []
for elem in duplicate_lst:
    cleaned_json = clean_and_parse_json(elem)
    cleaned_duplicate_list.append(cleaned_json)
cleaned_duplicate_list

Первая попытка не удалась: Expecting ',' delimiter: line 4 column 666 (char 721)
Первая попытка не удалась: Expecting ',' delimiter: line 4 column 401 (char 475)
Первая попытка не удалась: Expecting ',' delimiter: line 22 column 45 (char 1291)
Первая попытка не удалась: Expecting ',' delimiter: line 4 column 269 (char 352)
Первая попытка не удалась: Expecting ',' delimiter: line 4 column 354 (char 409)


[{'analysis': {'general_topic': 'изменение ВРИ',
   'answer': 'Добрый день! Информируем, что за изменение ВРИ на виды предусматривающие жилищное строительство взимается плата, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57. Первоначально необходимо обратиться за услугой "Предоставление расчета размера платы за изменение ВРИ земельного участка". Ссылка на услугу – "https://uslugi.mosreg.ru/services/21663" . Далее, после оплаты Вам необходимо обратиться в Управление Федеральной службы государственной регистрации, кадастра и картографии по Московской области (Росреестр), посредством обращения в любой центр государственных и муниципальных услуг "Мои документы" на территории Московской области за изменением вида разрешенного использования земельного участка.'},
  'themes': [{'theme_name': 'Платные изменения ВРИ',
    'question_count': 28,
    'description': 'Вопросы, связанные с изменением ВРИ на виды, предусматривающие жи

## Работа с уникальными парами

In [35]:
unique_pairs

[['Добрый день При заполнении услуги на последнем шаге требуется СОГЛАСИЕ СОБСТВЕННИКА ЗЕМЕЛЬНОГО УЧАСТКА НА УСТАНОВЛЕНИЕ СООТВЕТСТВИЯ ВИДА РАЗРЕШЕННОГО ИСПОЛЬЗОВАНИЯ ЗЕМЕЛЬНОГО УЧАСТКА, без которого невозможно перейти на последний шаг НО! В описании услуги в вопросах-ответах есть требование к документам: Согласие собственника(-ов) земельного участка на установление соответствия вида разрешенного использования земельного участка (в случае, если с заявлением обращается правообладатель, не являющийся собственником этого земельного участка); Я являюсь собственником (не представителем) участка Мне необходимо нотариально заверять заявление или возможно обойтись без этого или возможно ли сделать этот пункт при заполнении необязательным? Спасибо',
  'Добрый день! Если у вас высвечивается данный документ как обязательный, скорее всего вы ответили "да" на вопрос "ЗЕМЕЛЬНЫЙ УЧАСТОК НАХОДИТСЯ У ЗАЯВИТЕЛЯ В АРЕНДЕ/БЕЗВОЗМЕЗДНОМ ПОЛЬЗОВАНИИ/ПОСТОЯННОМ (БЕССРОЧНОМ) ПОЛЬЗОВАНИИ?" или "ЗЕМЕЛЬНЫЙ УЧАСТ

In [36]:
from tqdm.notebook import tqdm

# коверкает жестко ответы на вопросы по конкретным заялениям
sys_prompt_unique = '''
Ты анализируешь ответы, данные на пользовательские вопросы.

ИНСТРУКЦИЯ:
- Оцени пару "вопрос-ответ" по критериям ниже
- Прими решение: оставить ответ, улучшить ответ, немного переписав его по правилам, или удалить ответ, если он абсолютно не соответствует вопросу.

ПРАВИЛА:
- Улучшай (исправляй) только ответы на общие тематики. 
- Вноси только косметические исправления, направленные на улучшение читабельности. Строго запрещено менять смысл ответов.
- Никогда не исправляй ответы на вопросы по заявлениям, начинающимся на P001. У тебя нет доступа к ним и их статусам. Ты ничего не можешь менять.
- При исправлении ответов запрещено добавлять данные от себя - ты не знаешь детали процессов. Не пиши от себя никакие сроки, статусы, ресурсы.

КРИТЕРИИ ОЦЕНКИ:
- Полнота: отвечает ли на вопрос полностью?
- Уместность: логично ли сочетание вопроса и ответа?

ФОРМАТ ОТВЕТА:
{
    "query": "текст вопроса",
    "original_answer": "текст исходного ответа",
    "assessment": "оставить, переписать или удалить"
    "corrected_answer": "переписанный ответ | текст исходного ответа, если решено оставить как есть или удалить"
}
'''

unique_pairs_lst = []

for elem in tqdm(unique_pairs, desc="Обработка пар"):
    query = elem[0]
    answer = elem[1]
    user_prompt_unique = f'Вопрос пользователя: {query}. Ответ: {answer}'
    res = call_llm(model, url, sys_prompt=sys_prompt_unique, user_prompt=user_prompt_unique)
    unique_pairs_lst.append(res)

Обработка пар:   0%|          | 0/411 [00:00<?, ?it/s]

c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: Insecur

In [37]:
cleaned_unique_list = []
for elem in unique_pairs_lst:
    cleaned_unique_json = clean_and_parse_json(elem)
    cleaned_unique_list.append(cleaned_unique_json)

cleaned_unique_list

Первая попытка не удалась: Invalid control character at: line 5 column 630 (char 2513)
Первая попытка не удалась: Expecting ',' delimiter: line 2 column 439 (char 440)


[{'query': 'Добрый день При заполнении услуги на последнем шаге требуется СОГЛАСИЕ СОБСТВЕННИКА ЗЕМЕЛЬНОГО УЧАСТКА НА УСТАНОВЛЕНИЕ СООТВЕТСТВИЯ ВИДА РАЗРЕШЕННОГО ИСПОЛЬЗОВАНИЯ ЗЕМЕЛЬНОГО УЧАСТКА, без которого невозможно перейти на последний шаг НО! В описании услуги в вопросах-ответах есть требование к документам: Согласие собственника(-ов) земельного участка на установление соответствия вида разрешенного использования земельного участка (в случае, если с заявлением обращается правообладатель, не являющийся собственником этого земельного участка); Я являюсь собственником (не представителем) участка Мне необходимо нотариально заверять заявление или возможно обойтись без этого или возможно ли сделать этот пункт при заполнении необязательным? Спасибо.',
  'original_answer': 'Добрый день! Если у вас высвечивается данный документ как обязательный, скорее всего вы ответили "да" на вопрос "ЗЕМЕЛЬНЫЙ УЧАСТОК НАХОДИТСЯ У ЗАЯВИТЕЛЯ В АРЕНДЕ/БЕЗВОЗМЕЗДНОМ ПОЛЬЗОВАНИИ/ПОСТОЯННОМ (БЕССРОЧНОМ) ПОЛЬЗ

## Конкатенация данных

In [38]:
cleaned_duplicate_list

[{'analysis': {'general_topic': 'изменение ВРИ',
   'answer': 'Добрый день! Информируем, что за изменение ВРИ на виды предусматривающие жилищное строительство взимается плата, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57. Первоначально необходимо обратиться за услугой "Предоставление расчета размера платы за изменение ВРИ земельного участка". Ссылка на услугу – "https://uslugi.mosreg.ru/services/21663" . Далее, после оплаты Вам необходимо обратиться в Управление Федеральной службы государственной регистрации, кадастра и картографии по Московской области (Росреестр), посредством обращения в любой центр государственных и муниципальных услуг "Мои документы" на территории Московской области за изменением вида разрешенного использования земельного участка.'},
  'themes': [{'theme_name': 'Платные изменения ВРИ',
    'question_count': 28,
    'description': 'Вопросы, связанные с изменением ВРИ на виды, предусматривающие жи

In [39]:
cleaned_unique_list

[{'query': 'Добрый день При заполнении услуги на последнем шаге требуется СОГЛАСИЕ СОБСТВЕННИКА ЗЕМЕЛЬНОГО УЧАСТКА НА УСТАНОВЛЕНИЕ СООТВЕТСТВИЯ ВИДА РАЗРЕШЕННОГО ИСПОЛЬЗОВАНИЯ ЗЕМЕЛЬНОГО УЧАСТКА, без которого невозможно перейти на последний шаг НО! В описании услуги в вопросах-ответах есть требование к документам: Согласие собственника(-ов) земельного участка на установление соответствия вида разрешенного использования земельного участка (в случае, если с заявлением обращается правообладатель, не являющийся собственником этого земельного участка); Я являюсь собственником (не представителем) участка Мне необходимо нотариально заверять заявление или возможно обойтись без этого или возможно ли сделать этот пункт при заполнении необязательным? Спасибо.',
  'original_answer': 'Добрый день! Если у вас высвечивается данный документ как обязательный, скорее всего вы ответили "да" на вопрос "ЗЕМЕЛЬНЫЙ УЧАСТОК НАХОДИТСЯ У ЗАЯВИТЕЛЯ В АРЕНДЕ/БЕЗВОЗМЕЗДНОМ ПОЛЬЗОВАНИИ/ПОСТОЯННОМ (БЕССРОЧНОМ) ПОЛЬЗ

In [40]:
def combine_processed_data(dupl_list, unique_list):
    combined_data = []

    # начнем с дубликатов
    print("Извлечение канонических вопросов из групп дубликатов...")
    for group_idx, group in enumerate(dupl_list): # извлекаем ответы
        if group is None:
            print(f"⚠️ Группа {group_idx} равна None, пропускаем")
            continue
        answer = group.get('analysis').get('answer') 

        if not answer:
            print(f"⚠️ В группе {group_idx} нет ответа!")
            continue

        for theme in group.get('themes'):
            canonical_questions = theme.get('canonical_questions')
            for cq in canonical_questions:
                if cq and answer:

                    combined_data.append(
                        {
                        "question": cq,
                        "answer": answer
                        }
                    )

    # теперь уникальные вопросы
    print("Приступаем к извлечению уникальных ответов")
    for unique_idx, unique_elem in enumerate(unique_list): 
        if unique_elem is None:
            print(f"⚠️ Уникальная ВОП {unique_idx} равна None, пропускаем")
            continue
        
        assessment = unique_elem.get("assessment")
        query = unique_elem.get("query") 
        answ = unique_elem.get("corrected_answer")

        if assessment == "переписать" or assessment == "оставить": 
            combined_data.append(
                {
                    "question": query,
                    "answer": answ                
                }
            )
        else:
            pass

    return combined_data

In [41]:
result = combine_processed_data(cleaned_duplicate_list, cleaned_unique_list)
result

Извлечение канонических вопросов из групп дубликатов...
⚠️ Группа 1 равна None, пропускаем
⚠️ Группа 5 равна None, пропускаем
⚠️ Группа 17 равна None, пропускаем
⚠️ Группа 20 равна None, пропускаем
⚠️ Группа 45 равна None, пропускаем
Приступаем к извлечению уникальных ответов
⚠️ Уникальная ВОП 226 равна None, пропускаем
⚠️ Уникальная ВОП 398 равна None, пропускаем


[{'question': 'Какие действия необходимы для изменения вида разрешенного использования земельного участка на ИЖС, и какова стоимость этой процедуры?',
  'answer': 'Добрый день! Информируем, что за изменение ВРИ на виды предусматривающие жилищное строительство взимается плата, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57. Первоначально необходимо обратиться за услугой "Предоставление расчета размера платы за изменение ВРИ земельного участка". Ссылка на услугу – "https://uslugi.mosreg.ru/services/21663" . Далее, после оплаты Вам необходимо обратиться в Управление Федеральной службы государственной регистрации, кадастра и картографии по Московской области (Росреестр), посредством обращения в любой центр государственных и муниципальных услуг "Мои документы" на территории Московской области за изменением вида разрешенного использования земельного участка.'},
 {'question': 'Нужно ли платить за изменение ВРИ с садоводства 

## Постобработка данных
Как-то все портит

In [ ]:
# system_prompt_3 = """
# Ты - эксперт по обработке вопросно-ответных пар для госуслуг и земельных вопросов.

# ТВОИ ЗАДАЧИ для каждой пары:
# 1. ОЦЕНКА КАЧЕСТВА (1-5, где 1 - плохо, 5 - отлично)
#    - Ясность и полнота вопроса
#    - Точность и полезность ответа
#    - Соответствие ответа вопросу

# 2. ПРОВЕРКА НА КОНКРЕТИКУ (удалить если):
#    - Ответ содержит конкретные номера заявлений или земельных участков и говорит ТОЛЬКО про них
#    - Ситуация уникальна и никак не подходит для эталонного датасета

# 3. УЛУЧШЕНИЕ (если нужно):
#    - Обобщить конкретные детали до общей формулировки
#    - Дополнить неполные ответы
#    - Упростить сложные бюрократические формулировки

# ВАЖНО:
# - Сохраняй профессиональный стиль ответов
# - Не меняй смысл, только улучшай форму
# - Если вопрос слишком конкретный, но ценен - попробуй его обобщить
# - Если улучшение невозможно - удали ответ

# ФОРМАТ ОТВЕТА - как в исходной версии:
# {
#     "question": "текст вопроса",
#     "answer": "текст оригинального ответа | текст исправленного ответа"
# }
# """

# final_lst = []
# for elem in result:
#     user_prompt_3 = f'Вопросно-ответная пара: {elem}'
#     res = call_llm(model=model, url=url, sys_prompt=system_prompt_3, user_prompt=user_prompt_3)
#     final_lst.append(res)
# final_lst

c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: Insecur

['{\n    "question": "Какие действия необходимы для изменения вида разрешенного использования земельного участка на ИЖС, и какова стоимость этой процедуры?",\n    "answer": "Добрый день! Для изменения вида разрешенного использования земельного участка на индивидуальное жилищное строительство (ИЖС) необходимо: 1) подать заявление на получение расчета размера платы за изменение ВРИ через портал государственных услуг (https://uslugi.mosreg.ru/services/21663); 2) оплатить установленную плату, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57; 3) подать заявление в Управление Росреестра по Московской области (или в МФЦ «Мои документы») о внесении изменения в ЕГРН. Стоимость процедуры зависит от кадастровой стоимости участка и категории земель, а также включает государственную пошлину за регистрацию изменений. Рекомендуем уточнять актуальные тарифы на официальном портале mosreg.ru."\n}',
 '{\n    "question": "Нужно ли платить 

In [ ]:
# cleaned_almost_final_list = []
# for e in final_lst:
#     cleaned_almost_final_json = clean_and_parse_json(e)
#     cleaned_almost_final_list.append(cleaned_almost_final_json)
# cleaned_almost_final_list

Первая попытка не удалась: Invalid control character at: line 3 column 134 (char 245)
Первая попытка не удалась: Extra data: line 6 column 1 (char 2332)
Первая попытка не удалась: Extra data: line 6 column 1 (char 2289)
Первая попытка не удалась: Extra data: line 6 column 1 (char 2013)
Первая попытка не удалась: Extra data: line 6 column 1 (char 1878)
Первая попытка не удалась: Extra data: line 6 column 1 (char 1746)


[{'question': 'Какие действия необходимы для изменения вида разрешенного использования земельного участка на ИЖС, и какова стоимость этой процедуры?',
  'answer': 'Добрый день! Для изменения вида разрешенного использования земельного участка на индивидуальное жилищное строительство (ИЖС) необходимо: 1) подать заявление на получение расчета размера платы за изменение ВРИ через портал государственных услуг (https://uslugi.mosreg.ru/services/21663); 2) оплатить установленную плату, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57; 3) подать заявление в Управление Росреестра по Московской области (или в МФЦ «Мои документы») о внесении изменения в ЕГРН. Стоимость процедуры зависит от кадастровой стоимости участка и категории земель, а также включает государственную пошлину за регистрацию изменений. Рекомендуем уточнять актуальные тарифы на официальном портале mosreg.ru.'},
 {'question': 'Нужно ли платить за изменение ВРИ с с

In [ ]:
# system_prompt_4 = """
# Ты эксперт-редактор базы знаний госуслуг. 
# ЗАДАЧА: привести вопросно-ответные пары по подаче заявлений через портал РПГУ к единому стандарту.
# ---
# ТРИГГЕР ДЛЯ ПРАВКИ:
# Редактируй ответ ТОЛЬКО если в нем описывается технический алгоритм подачи заявления через РПГУ (упоминаются фразы: "авторизоваться в ЕСИА", "заполнить электронную форму", "портал РПГУ", "прикрепить документы").

# ПРИМЕР ОТВЕТА ДЛЯ РЕДАКЦИИ:
# "Добрый день! Для подачи заявки Вам необходимо обратиться через РПГУ. В качестве заявления выступает электронная форма, которая подписывается простой электронной подписью - авторизацией в ЕСИА. 
# Чтобы подать заявление в электронном виде заявителю (представителю заявителя) необходимо: 
# • авторизоваться в Единой системе идентификации и аутентификации (ЕСИА*); 
# • выбрать необходимую услугу на РПГУ; 
# • заполнить электронную форму заявления; 
# • прикрепить электронные образы необходимых документов; 
# • отправить заявление с приложенными документами на рассмотрение. 
# *При авторизации через ЕСИА заявление считается подписанным простой электронной подписью заявителя (представителя заявителя, уполномоченного на подписание заявления)."
# ---
# ИНСТРУКЦИЯ ПО РЕДАКТИРОВАНИЮ:
# Если триггер сработал:
# 1. Замени громоздкое описание процесса на стандартный ШАБЛОН ДЛЯ ЗАМЕНЫ (см. ниже).
# 2. Сохрани информацию о конкретной услуге, если она упоминалась в начале оригинального ответа.
# 3. Если ответ НЕ описывает технический алгоритм подачи (например, это просто консультация по закону), ОСТАВЬ ТЕКСТ БЕЗ ИЗМЕНЕНИЙ.

# ШАБЛОН ДЛЯ ЗАМЕНЫ:
# "Для подачи заявки Вам необходимо подать заявление через РПГУ. В качестве заявления выступает электронная форма, которая подписывается простой электронной подписью. 
# Заявителю (представителю заявителя) необходимо: 
# • авторизоваться в Единой системе идентификации и аутентификации (ЕСИА*); 
# • заполнить электронную форму заявления; 
# • прикрепить электронные образы необходимых документов; 
# • отправить заявление с приложенными документами на рассмотрение. 
# *При авторизации через ЕСИА заявление считается подписанным простой электронной подписью заявителя (представителя заявителя, уполномоченного на подписание заявления)."
# ---
# ФОРМАТ ВЫХОДА (СТРОГИЙ JSON):
# {
#     "question": "оригинальный текст вопроса",
#     "answer": "исправленный текст по шаблону ИЛИ оригинальный текст, если правок не было"
# }

# Никаких вводных слов и пояснений, только JSON.
# """

# final_lst_2 = []
# for elem in cleaned_almost_final_list:
#     # print(f'elem: {elem}')
#     user_prompt_4 = f'Вопрос и ответ: {elem}'
#     resss = call_llm(model=model, url=url, sys_prompt=system_prompt_4, user_prompt=user_prompt_4)
#     # print(resss)
#     final_lst_2.append(resss)
# final_lst_2

c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host '10.44.123.3'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Projects\MIO\.venv\Lib\site-packages\urllib3\connectionpool.py:1097: Insecur

['{\n    "question": "Какие действия необходимы для изменения вида разрешенного использования земельного участка на ИЖС, и какова стоимость этой процедуры?",\n    "answer": "Добрый день! Для изменения вида разрешенного использования земельного участка на индивидуальное жилищное строительство (ИЖС) необходимо: 1) подать заявление на получение расчета размера платы за изменение ВРИ через портал государственных услуг (https://uslugi.mosreg.ru/services/21663); 2) оплатить установленную плату, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57; 3) подать заявление в Управление Росреестра по Московской области (или в МФЦ «Мои документы») о внесении изменения в ЕГРН. Стоимость процедуры зависит от кадастровой стоимости участка и категории земель, а также включает государственную пошлину за регистрацию изменений. Рекомендуем уточнять актуальные тарифы на официальном портале mosreg.ru."\n}',
 '{\n    "question": "Нужно ли платить 

In [ ]:
# cleaned_very_final_list = []
# for elem in final_lst_2:
#     cleaned_very_final_json = clean_and_parse_json(elem)
#     cleaned_very_final_list.append(cleaned_very_final_json)
# cleaned_very_final_list

Первая попытка не удалась: Invalid control character at: line 3 column 531 (char 685)
Первая попытка не удалась: Invalid control character at: line 3 column 180 (char 264)
Первая попытка не удалась: Invalid control character at: line 3 column 217 (char 297)
Первая попытка не удалась: Invalid control character at: line 3 column 259 (char 381)
Первая попытка не удалась: Invalid control character at: line 3 column 180 (char 306)
Первая попытка не удалась: Invalid control character at: line 3 column 180 (char 259)
Первая попытка не удалась: Invalid control character at: line 3 column 399 (char 511)


[{'question': 'Какие действия необходимы для изменения вида разрешенного использования земельного участка на ИЖС, и какова стоимость этой процедуры?',
  'answer': 'Добрый день! Для изменения вида разрешенного использования земельного участка на индивидуальное жилищное строительство (ИЖС) необходимо: 1) подать заявление на получение расчета размера платы за изменение ВРИ через портал государственных услуг (https://uslugi.mosreg.ru/services/21663); 2) оплатить установленную плату, размер которой определяется в соответствии с Постановлением Правительства Московской области от 31.12.2013 №1190/57; 3) подать заявление в Управление Росреестра по Московской области (или в МФЦ «Мои документы») о внесении изменения в ЕГРН. Стоимость процедуры зависит от кадастровой стоимости участка и категории земель, а также включает государственную пошлину за регистрацию изменений. Рекомендуем уточнять актуальные тарифы на официальном портале mosreg.ru.'},
 {'question': 'Нужно ли платить за изменение ВРИ с с

In [46]:
# test
# texxt = '''
# {'question': 'Какие шаги нужно выполнить для подачи заявления в электронной форме?',
#  'answer': 'Добрый день! Для подачи заявки Вам необходимо обратиться через РПГУ. В качестве заявления выступает электронная форма, которая подписывается простой электронной подписью - авторизацией в ЕСИА. Чтобы подать заявление в электронном виде заявителю (представителю заявителя) необходимо: • авторизоваться в Единой системе идентификации и аутентификации (ЕСИА*); • выбрать необходимую услугу на РПГУ; • заполнить электронную форму заявления; • прикрепить электронные образы необходимых документов; • отправить заявление с приложенными документами на рассмотрение. *При авторизации через ЕСИА заявление считается подписанным простой электронной подписью заявителя (представителя заявителя, уполномоченного на подписание заявления).'},

# '''

# user_prompt_5 = f'Вопрос и ответ: {texxt}'
# res_5 = call_llm(model=model, url=url, sys_prompt=system_prompt_4, user_prompt=user_prompt_5)
# res_5

## Сбор файла

In [48]:
# без финальной обработки

def to_markdown(combined_data, output_file="1_VOP_new_5.md"):
    
    print(f"Создание .md файла из {len(combined_data)} пар...")
    
    with open(output_file, 'w', encoding='utf-8') as f:
            
        for i, pair in enumerate(combined_data):
            if pair is None:
                print("Группа равна None")
                continue
            question = pair.get('question', '').strip()
            answer = pair.get('answer', '').strip()
            
            if not question or not answer:
                print(f"⚠️ Пара {i} пропущена: пустой вопрос или ответ")
                continue
            
            # Заголовок второго уровня
            f.write(f"## {question}\n")
            # Ответ
            f.write(f"{answer}\n\n\n")
            
            # Прогресс
            if (i + 1) % 100 == 0:
                print(f"  Обработано {i + 1} пар...")
    
    print(f"\n✅ Файл создан: {output_file}")
    print(f"Всего записано пар: {len(combined_data)}")
    
    return output_file

to_markdown(result)

Создание .md файла из 634 пар...
  Обработано 100 пар...
  Обработано 200 пар...
  Обработано 300 пар...
  Обработано 400 пар...
  Обработано 500 пар...
  Обработано 600 пар...

✅ Файл создан: 1_VOP_new_5.md
Всего записано пар: 634


'1_VOP_new_5.md'